# Tabla de contenido
| Sección                      | Subsección            |
|-------------------------------|----------------------------|
|[Introducción](#introduccion)|[Datasets](#datasets)|
|[Analisis Exploratorio](#analisis-exploratorio)| [Hallazgos Iniciales](#hallazgos-iniciales), [Outliers](#identificacion-de-outliers)|
|[Valores criticos](#valores-críticos)|[Viajes por dia](#viajes-por-dia)|



| Variable                     | Descripción               |
|-------------------------------|----------------------------|
truck|Código de camión 
loader|Código de pala 
ton|Tonelaje con que ser carga camión
n_shovel|Número de paladas que fueron necesarias para cargar camión
truck_total_cycle|Ciclo total de camión (s)
loader_total_cycle|Ciclo total pala (s) 
distance_empty|Distancia que recorre CAEX vacío (m)
distance_full|Distancia que recorre CAEX lleno (m)
date|Fecha toma de registro



Contexto
Esto implica, que cualquier ahorro generado
por una mejora en la carga y el acarreo impactan directamente en un costo menor por tonelada de material
transportado [MODELO CONCEPTUAL DE SISTEMAS DE CARGA Y ACARREO DE MINERAL EN MINAS A CIELO ABIERTO, Salomón Liliana1
; Ortiz Alexis2 ]


https://es.linkedin.com/pulse/optimizaci%C3%B3n-y-simulaci%C3%B3n-de-minas-jorge-lozano

https://www.youtube.com/watch?v=KAK0RrkC2Qo

In [1]:
import pandas as pd
from ydata_profiling import ProfileReport
import scipy.stats as stats
from statistics import mode

import plotly.express as px
import plotly.graph_objects as go
import plotly.subplots as sp
import matplotlib.pyplot as plt
from ipywidgets import interact, Dropdown, widgets
from IPython.display import display

In [2]:
###Carga de archivo
df = pd.read_csv(r'data\timeseries_haul_loading_data.csv')
df['date']=pd.to_datetime(df['date'])
# df = df.set_index('date')
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 395680 entries, 0 to 395679
Data columns (total 9 columns):
 #   Column              Non-Null Count   Dtype         
---  ------              --------------   -----         
 0   truck               395680 non-null  object        
 1   loader              395680 non-null  object        
 2   ton                 395680 non-null  float64       
 3   n_shovel            395680 non-null  float64       
 4   truck_total_cycle   395680 non-null  float64       
 5   loader_total_cycle  395680 non-null  float64       
 6   distance_empty      395680 non-null  float64       
 7   distance_full       395680 non-null  float64       
 8   date                395680 non-null  datetime64[ns]
dtypes: datetime64[ns](1), float64(6), object(2)
memory usage: 27.2+ MB


## Análisis exploratorio

En la primera parte del análisis exploratorio se usará la libreria de autoreporting ydata_profiling. En la sección de hallazgos se discute sobre la calidad de la data.

In [3]:
profile = ProfileReport(df, title="Profiling Report")
profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [4]:
## Estadísticas básicas con desviación estándar
df.describe()

ton       n_shovel  truck_total_cycle  loader_total_cycle   
count  395680.000000  395680.000000      395680.000000       395680.000000  \
mean      318.007490       3.316556        2284.313481          305.073340   
min         0.000000       3.000000          23.000000            0.000000   
25%       305.666647       3.000000        1633.000000          217.000000   
50%       317.758250       3.000000        2134.000000          303.000000   
75%       330.125978       4.000000        2945.000000          390.000000   
max       384.927167      15.000000       15812.000000        11692.000000   
std        18.124753       0.558689         856.620246          116.657122   

       distance_empty  distance_full                           date  
count   395680.000000  395680.000000                         395680  
mean      6161.241612    5782.712235  2023-09-30 18:52:34.185200128  
min        512.000000     504.000000            2023-01-01 00:00:00  
25%       3931.000000    3754.000000            2023-05-23 00:00:00  
50%       6009.000000    5412.000000            2023-10-20 00:00:00  
75%       8059.000000    7798.000000            2024-02-04 00:00:00  
max      15783.000000   15691.000000            2024-05-24 00:00:00  
std       2569.465489    2355.404982                            NaN

### Hallazgos iniciales
    
- **Datos categóricos**: 2 `truck`, `loader`<br>
    
    - `truck` tiene 47 valores únicos (47 camiones),
    - `loader` solo tiene 4 valores únicos (4 tipos de palas). En funcion de su utilizacion de mayor a menor esta `PH58 > PH48 > PH06 > PH55`
- **Datos faltantes**: No hay datos faltantes!

- La serie de tiempo abarca desde `2023-01-01` hasta `2024-05-24`.`

- **Datos numéricos**: 6
    
   - El tonelaje (`ton`) promedio de carga es bastante consistente siendo de 318.00 t +/- 18.12. En promedio se requieren 3.32 paladas (`n_shovel`) para cargar un camión, la variabilidad aquí también es baja, sugiriendo una **estandarización en las operaciones de carga**. 
   - Los ciclos totales, tanto para camiones (`truck_total_cycle`) como para palas (`loader_total_cycle`), muestran una mayor variabilidad, lo que podría indicar **diferencias en la eficiencia o en las condiciones operativas a lo largo del tiempo**. 
   - Existe una fuerte correlación entre `truck_total_cycle` y las distancias recorridas, tanto vacias (`distance_empty`) como llenas (`distance_full`), es decir, hay una relación directa entre el tiempo que un camión pasa en operación y la distancia que recorre, lo que podria tener implicaciones de eficiencia en **costos operativos** (más combustible y mantenimiento/desgaste), o la necesidad de mejorar la planificación de rutas.
   
   _Esto último no será considera en este análsis puesto que no se cuenta con información geográfica, pero vale la pena señalarlo_.



## Identificacion de outliers
Como primer paso se identifican y eliminan los outliers, definidos como aquellos valores que se encuentran por encima del percentil 99 o por debajo del percentil 1 para cada variable numérica de tipo flotante. Estos valores extremos se filtran del conjunto de datos principal para evitar que distorsionen los análisis de tendencias y relaciones entre variables; sin embargo, se preservan en un conjunto de datos separado, permitiendo así un análisis paralelo de los comportamientos atípicos sin interferir en los resultados del análisis general que serán los que definan nuestros objetivos y comportamientos estandard para la operación.

Posteriormente, se analizan los viajes realizdos por dia y la inactividad de las flotas. Tambien alli se encuentran valores atipicos que seran descartados

In [3]:
df_filtered = df.copy()
numeric_cols= df.select_dtypes(include=['float64']).columns
numeric_cols=numeric_cols.drop('n_shovel')
outliers_df = pd.DataFrame()

for col in numeric_cols:
    lower_bound = df[col].quantile(0.01)
    upper_bound = df[col].quantile(0.99)
    
    # Extraer los valores que están fuera de los percentiles 1 y 99
    outliers = df[(df[col] < lower_bound) | (df[col] > upper_bound)]
    
    # Concatenar los outliers en el DataFrame de outliers
    outliers_df = pd.concat([outliers_df, outliers])

    # Filtrar los valores que están dentro del rango y asignarlos a df_filtered
    df_filtered = df_filtered[(df_filtered[col] >= lower_bound) & (df_filtered[col] <= upper_bound)]

outliers_df=outliers_df.drop_duplicates()

print(f'El porcentaje de outliers eliminado es de {round(outliers_df.shape[0]/df.shape[0]*100,2)}%')

El porcentaje de outliers eliminado es de 8.6%


Como resultado de este proceso, se elimina el 8.6% de los datos originales. Dado el tamaño total del dataset, esta reducción es aceptable, ya que permite obtener una muestra representativa y mejorar la precisión en el análisis de eficiencia sin perder un volumen significativo de datos. Finalmente, para contrastar las distribuciones originales con las obtenidas después del filtrado de outliers, se realizan gráficos Q-Q independientes para cada variable en ambos conjuntos de datos, lo que facilita la evaluación del impacto de los outliers en la normalidad de las distribuciones.

_Note que para ver los graficos interactivos se debe ejectuar el notebook_

In [6]:
@interact(variable=[var for var in df.columns if df[var].dtype in ['float64']])
def plot_qq(variable):
    plt.figure(figsize=(12, 6))

    # Gráfico Q-Q para el DataFrame original
    plt.subplot(1, 2, 1)
    stats.probplot(df[variable], dist="norm", plot=plt)
    plt.title(f'Gráfico Q-Q Original para {variable}')
    plt.grid(True)

    # Gráfico Q-Q para el DataFrame filtrado (sin outliers)
    plt.subplot(1, 2, 2)
    stats.probplot(df_filtered[variable], dist="norm", plot=plt)
    plt.title(f'Gráfico Q-Q Sin Outliers para {variable}')
    plt.grid(True)

    plt.tight_layout()
    plt.show()

interactive(children=(Dropdown(description='variable', options=('ton', 'n_shovel', 'truck_total_cycle', 'loade…

La mayoría de los datos eliminados corresponden a valores atípicos en la variable `truck_total_cycle` y `loader_total_cycle`. 
En general, los puntos presentan una curvatura en las colas, lo que indica que no siguen una distribución normal y sugiere una distribución sesgada. En lugar de realizar transformaciones para normalizar los datos, se optará por implementar modelos de machine learning robustos a distribuciones no normales.


#### Viajes diarios por camión

Antes de realizar el análisis de eficiencia/rendimiento en función del tonelaje, se ha generado un heatmap que muestra el número de viajes realizados diariamente por cada camión. Este gráfico permite observar, de manera visual, la distribución de la carga de trabajo entre los camiones a lo largo del tiempo, ayudando a detectar patrones consistentes o días específicos con actividad inusualmente alta o baja. Esta información es esencial para comprender la utilización diaria de cada camión y determinar posibles oportunidades de optimización en el flujo de trabajo.

In [4]:
trucks_n=df_filtered.drop(columns=['n_shovel']).groupby(['truck','date']).sum(numeric_only=True).reset_index()
trips_per_day = df_filtered.groupby(['truck', 'date']).size().reset_index(name='trips')

trucks=pd.merge(trucks_n,trips_per_day, on = ['truck', 'date'], how='left')
trucks.sample(4)

truck       date          ton  truck_total_cycle  loader_total_cycle   
19030  CAEX85 2024-04-21  9944.031345            55573.0              8981.0  \
10746  CAEX49 2023-12-01  6435.271312            36662.0              5825.0   
3489   CAEX22 2023-11-26  6408.436448            34920.0              6751.0   
12969  CAEX58 2023-05-06  4885.560405            38104.0              5279.0   

       distance_empty  distance_full  trips  
19030        122402.0       121521.0     31  
10746         89854.0        90771.0     20  
3489          81343.0        77873.0     20  
12969        112997.0        90245.0     16

In [5]:
heatmap_data = trucks.pivot(index='truck', columns='date', values='trips')

height = max(600, 20 * len(df['truck'].unique()))
custom_scale = [
    [0.0, 'rgb(222,217,226)'],  # valores más bajos
    [0.5, 'rgb(192,185,221)'],  # valores medios
    [1.0, 'rgb(117,201,200)']       # más oscuro para los valores más altos
]

fig = px.imshow(heatmap_data,
                labels=dict(x="Fecha", y="Camión", color="Viajes"),
                x=heatmap_data.columns.strftime('%Y-%m-%d'),  # Formatea las fechas para visualización
                aspect="auto",
                color_continuous_scale=custom_scale,
                ) 

fig.update_layout(
    title='Heatmap de Viajes por Camión y Día',
    xaxis_title='Fecha',
    yaxis_title='Camión',
    yaxis={'dtick':1},
    height=height
)

fig.show()


En el heatmap se observa que existen 9 camiones con un mayor  número de viajes diarios en comparación con el resto de la flota. Es importante evaluar si estos valores podrían establecerse como referencia objetivo para los demás vehículos:

- `CAEX25`
- `CAEX31`
- `CAEX41`
- `CAEX44`
- `CAEX55`
- `CAEX66`
- `CAEX81`
- `CAEX93`
- `CAEX98`

Ademas, se destacan los "huecos" o días en los que algunos equipos no registran actividad. Estos periodos sin viajes pueden reflejar tiempos de inactividad programados, como mantenimiento, o incluso interrupciones no planificadas. 

A partir de estos vacíos, resulta útil calcular el tiempo de inactividad diario para cada camión, para entender mejor la disponibilidad operativa y la eficiencia de la flota que permintan identificar oportunidades de optimización en la gestión de recursos.
El cálculo de inactividad se basa en el supuesto de que la operación es continua, es decir, se dispone de 24 horas de actividad al día para la flota.

In [6]:
tiempo_disponible_por_dia = 24  # 24 horas

# Tiempo activo total por día
inactividad_por_dia = df_filtered.groupby(['truck', 'date']).agg(
    tiempo_activo=('truck_total_cycle', 'sum')  
).reset_index()

#Calcular el tiempo inactivo y pasarlo a horas para que sea mas facil de visualizar
inactividad_por_dia['tiempo_inactivo'] = tiempo_disponible_por_dia - (inactividad_por_dia['tiempo_activo']/3600)
inactividad_por_dia['tiempo_activo'] = inactividad_por_dia['tiempo_activo']/3600

print(round(inactividad_por_dia,1).sample(5))
print(inactividad_por_dia.describe())

        truck       date  tiempo_activo  tiempo_inactivo
16807  CAEX74 2023-02-24           10.7             13.3
503    CAEX07 2023-01-30           10.0             14.0
8471   CAEX42 2024-04-30            7.8             16.2
7396   CAEX39 2023-12-19            4.0             20.0
9241   CAEX46 2023-09-12            9.8             14.2
                                date  tiempo_activo  tiempo_inactivo
count                          21938   21938.000000     21938.000000
mean   2023-09-11 00:07:21.097638656      10.389954        13.610046
min              2023-01-01 00:00:00       0.199444       -24.809167
25%              2023-05-06 00:00:00       6.448403        10.695764
50%              2023-09-11 00:00:00       9.719722        14.280278
75%              2024-01-15 00:00:00      13.304236        17.551597
max              2024-05-24 00:00:00      48.809167        23.800556
std                              NaN       5.806063         5.806063


Los valores de inactividad tienen valores atípicos que superan las 24 horas de trabajo (_valores menores a 0_), lo cual indica posibles inconsistencias en los registros, que podrían corresponder a errores en la captura o reportes irregulares. 

Al analizar los camiones que presentan estas anomalías, se observa que coinciden con los 9 camiones identificados anteriormente como los que realizan la mayor cantidad de viajes por día. Por lo tanto, es crucial monitorear esta parte de la flota para garantizar la precisión y la fiabilidad de los registros operativos.

In [7]:
print(inactividad_por_dia[inactividad_por_dia['tiempo_inactivo'] < 0]['truck'].unique())

['CAEX25' 'CAEX31' 'CAEX41' 'CAEX44' 'CAEX55' 'CAEX66' 'CAEX81' 'CAEX93'
 'CAEX98']


### Tonelaje por dia

Se analizara sin tener en cuenta los datos de registros poco confiables encontrados en el apartado anterior. Es decir, los que tengan tiempos inactivos con valores menores a 0 (han trabajado mas de 24 horas)

In [8]:
mascara = inactividad_por_dia[inactividad_por_dia['tiempo_inactivo'] >= 0]
df_inactividad = df_filtered[df_filtered.set_index(['truck', 'date']).index.isin(mascara.set_index(['truck', 'date']).index)]
print(f'El porcentaje de outliers eliminado es de {round(mascara.shape[0]/df.shape[0]*100,2)}%')

truck_ton_by_day = df_inactividad.groupby(['truck','date']).agg({
    'ton':'sum',
    'date':'size'
    }).rename(columns={'date':'trips'}).reset_index()

fig = px.box(truck_ton_by_day, x='truck', y='ton', title='Distribución de Toneladas/dia por Camión')
fig.update_layout(xaxis_title='Camión', yaxis_title='ton/dia', xaxis={'categoryorder':'total descending'})
fig.update_traces(marker_color='rgb(192,185,221)')
fig.show()


El porcentaje de outliers eliminado es de 5.37%


Aunque se han eliminado los valores atípicos correspondientes a registros de inactividad, los 9 camiones que transportan la mayor cantidad de toneladas diarias permanecen como referencia para definir un buen rendimiento.

En el siguiente gráfico se observa la evolución general del tonelaje transportado diariamente a lo largo del tiempo. Los días con valores bajos de tonelaje no se relacionan con un menor número de unidades operativas, ya que este número se mantiene relativamente constante entre `41 y 46` unidades al día. Esto indica que es necesario optimizar la eficiencia de la operación para mejorar el rendimiento general.

De acuerdo con las estadísticas de toneladas transportadas diariamente, estableceremos objetivos específicos para monitorear y optimizar la operación. Tomaremos los valores del 25º percentil (`176.955 toneladas`) y del 75º percentil (`238.353 toneladas`) como referencias clave para evaluar el rendimiento diario general. 

In [9]:
tonnage_per_day = df_inactividad.groupby(['date'])['ton'].sum().reset_index()
units_per_day = df_inactividad.groupby('date')['truck'].nunique().reset_index()
units_per_day.columns = ['date', 'num_units']  # Renombrar columna para claridad
print(f'Estadisticas para tonelaje total movido al dia\n{round(tonnage_per_day.describe(),1)}\n{round(units_per_day.describe(),1)}')

fig = sp.make_subplots(rows=2, cols=1, shared_xaxes=True, row_heights=[0.7, 0.3], vertical_spacing=0.1)

# Añadir serie de tonelaje
fig.add_trace(go.Scatter(
    x=tonnage_per_day['date'],
    y=tonnage_per_day['ton'],
    mode='lines',
    name='Tonelaje Diario',
    line=dict(color='rgb(162,200,215)')
), row=1, col=1)

# Añadir serie de número de camiones en subgráfica más pequeña
fig.add_trace(go.Scatter(
    x=units_per_day['date'],
    y=units_per_day['num_units'],
    mode='lines',
    name='Número de Camiones por Día',
    line=dict(color='rgb(192,185,221)')
), row=2, col=1)

# Configurar layout
fig.update_layout(
    title="Tonelaje Movido y Número de Camiones Utilizados por Día",
    xaxis_title="Fecha",
    yaxis=dict(title="Tonelaje"),
    yaxis2=dict(title="Número de Camiones"),
    template="plotly_white",
    height=600,
    hovermode="x unified"  # Puntero vertical sincronizado
)

fig.show()


Estadisticas para tonelaje total movido al dia
                                date       ton
count                            509     509.0
mean   2023-09-12 04:00:28.290766336  206797.4
min              2023-01-01 00:00:00   26612.5
25%              2023-05-08 00:00:00  176955.0
50%              2023-09-12 00:00:00  205312.7
75%              2024-01-17 00:00:00  238353.8
max              2024-05-24 00:00:00  359368.4
std                              NaN   48587.0
                                date  num_units
count                            509      509.0
mean   2023-09-12 04:00:28.290766336       41.7
min              2023-01-01 00:00:00       26.0
25%              2023-05-08 00:00:00       41.0
50%              2023-09-12 00:00:00       42.0
75%              2024-01-17 00:00:00       43.0
max              2024-05-24 00:00:00       46.0
std                              NaN        2.4


## Clustering para Segmentación de Equipos Basado en Rendimiento:

Ahora se realizara un clustering para segmentar basados en rendimiento y asi poder revelar patornes como cuales combinaciones de palas y cambiones trabajan mejor juntos, ayudando a identificar grupos de alto y bajo rendimiento, y explorar las características operativas que diferencian estos grupos, lo que puede informar estrategias de asignación de recursos.

Por fines de hacer el reporte mas ligero, este notebook se terminara en este punto dejando el csv necesario para el clustering. 

In [13]:
truck_loader_day_n=df_inactividad.groupby(['truck','date','loader']).sum(numeric_only=True).reset_index()
trips_per_day_l = df_inactividad.groupby(['truck', 'date','loader']).size().reset_index(name='trips')

truck_loader_day=pd.merge(truck_loader_day_n,trips_per_day_l, on = ['truck', 'date','loader'], how='left')
truck_loader_day.sample(4)

truck       date loader          ton  n_shovel  truck_total_cycle   
20850  CAEX41 2024-03-17   PH58  3809.250531      39.0            19609.0  \
10933  CAEX24 2023-02-05   PH58  4185.426668      40.0            41309.0   
25237  CAEX47 2023-06-22   PH58  1230.408875      13.0            10239.0   
27140  CAEX48 2024-04-09   PH48   327.889962       3.0             1693.0   

       loader_total_cycle  distance_empty  distance_full  trips  
20850              3134.0         56295.0        57717.0     12  
10933              3867.0         94672.0       101119.0     13  
25237              1404.0         31181.0        25372.0      4  
27140               110.0          4325.0         4222.0      1

In [14]:
### Guardar archivos para posterior uso
df_inactividad.to_csv(r'data\estandar.csv')
outliers_df.to_csv(r'data\outliers.csv')
truck_loader_day.to_csv(r'data\truck_loader_day.csv')

### Dashboards Interactivos
#### Dashboard de Monitoreo de Rendimiento Diario:

KPIs Relevantes:
Tonelaje total movido por día por equipo.
Ciclos totales de carga por camión y pala.
Eficiencia de carga (tonelaje por palada).
Tiempos de ciclo (ciclo total del camión y de la pala).
Características:
Filtros interactivos por fecha, tipo de equipo, y código de equipo.
Gráficos de tendencias de rendimiento a lo largo del tiempo.
Tablas de clasificación que se actualizan dinámicamente para mostrar los equipos de mejor rendimiento.

#### Dashboard de Análisis de Factores Críticos:

KPIs Relevantes:
Correlaciones entre variables operativas y tonelaje movido.
Importancia de las variables (basada en modelos predictivos).
Distribuciones de las variables clave por segmentos de alto y bajo rendimiento.
Características:
Visualizaciones de calor y gráficos de dispersión para explorar relaciones entre variables.
Histogramas y gráficos de cajas para analizar la distribución de variables críticas.
Mapas de calor para mostrar la correlación entre diferentes variables y el rendimiento.